In [40]:
from pymongo import MongoClient
import folium
import numpy as np
import pandas as pd

In [41]:
def connectCollection(database, collection):
    client = MongoClient()
    db = client[database]
    coll = db[collection]
    return db, coll

In [42]:
db, coll = connectCollection('companies','companies')

In [43]:
def getLocation(comp,i):
    latitude = comp['offices'][i]['latitude']
    longitude = comp['offices'][i]['longitude']
    loc = {
        'type':'Point',
        'coordinates':[longitude, latitude]
    }
    return loc

In [44]:
def getName(comp,i):
    name = comp['name']
    return name

I am going to filter all companies that have been founded after 2003, that have raised at least 1M dollars and that have a category code similar to a gaming company.

In [45]:
pipeline = [
    { "$unwind": "$offices"},
    {"$match":{ "$and": [  {"founded_year":{"$gt":2003}},
            {"funding_rounds.raised_amount":{"$gt":1000000}}, { "$or":[{"category_code":"web"},
            {"category_code":"software"},{"category_code":"games_video"},
            {"category_code":"hardware"},{"category_code":"mobile"},{"category_code":"music"},
            {"category_code":"photo_video"},{"category_code":"design"}]}] }}
#    {"$match":"}
    ]
results = list(coll.aggregate(pipeline))

In [46]:
name = []
city = []
country_code = []
longitude = []
latitude = []

for e in results:
    name.append(e["name"])
    city.append(e['offices']["city"])
    country_code.append(e['offices']["country_code"])
    for c in e["offices"].items():
        if c[0]=="longitude":
            longitude.append(c[1])
        elif c[0]=="latitude":
            latitude.append(c[1])

In [47]:
print(len(name),len(city),len(country_code),len(longitude),len(latitude))

1211 1211 1211 1211 1211


In [48]:
myData = {"name":name, "city":city, "country":country_code, "latitude":latitude, "longitude":longitude}

In [49]:
startup_df = pd.DataFrame(data=myData)

In [50]:
startup_df

name  \
0                                              Wetpaint   
1                                              Wetpaint   
2                                                  Geni   
3                                               Slacker   
4                                                 Joost   
5                                              Babelgum   
6                                                Mahalo   
7                                                  Kyte   
8                                                  Veoh   
9                                                Wesabe   
10                                      Jingle Networks   
11                                            Jangl SMS   
12                                                Jajah   
13                                               blogTV   
14                                         AdaptiveBlue   
15                                       Pando Networks   
16                                           Livestream   
17                                              Ustream   
18                                              Ustream   
19                                              Ustream   
20                                         GrandCentral   
21                                              YouTube   
22                                               CastTV   
23                                            SellABand   
24                                             SodaHead   
25                                            Revision3   
26                                         Funny Or Die   
27                                                  EQO   
28                                               iSkoot   
29                                               iSkoot   
30                                           Pageflakes   
31                                             Netvibes   
32                                             Netvibes   
33                                           FeedBurner   
34                                                 WeFi   
35                                               TVtrip   
36                                                 Bebo   
37                                              RockYou   
38                                              FlickIM   
39                                               Loomia   
40                                             Terabitz   
41                                                Meebo   
42                                                Meebo   
43                                                Meebo   
44                                                Meebo   
45                                                Meebo   
46                                             Newsvine   
47                                           Eventbrite   
48                                            coComment   
49                                         Hotelicopter   
50                                               Zvents   
51                                             Eventful   
52                                             Eventful   
53                                              Seesmic   
54                                                 ooma   
55                                             Flixster   
56                                                oDesk   
57                                              GoingOn   
58                                               spigit   
59                                               spigit   
60                                               spigit   
61                                          Bazaarvoice   
62                                               Indeed   
63                                               Indeed   
64                                                Jaxtr   
65                                          Respectance   
66                                               PeerMe   
67                                     

Here I could use geocoding to obtain the null coordinates with the address of each offices, but for simplifying purposes, I am going to get rid of them.

In [51]:
startup_clean = startup_df.dropna()

In [52]:
startup_clean

name                 city country   latitude  \
0                            Wetpaint              Seattle     USA  47.603122   
1                            Wetpaint             New York     USA  40.723731   
2                                Geni       West Hollywood     USA  34.090368   
3                             Slacker            San Diego     USA  33.022176   
4                               Joost             New York     USA  40.746497   
5                            Babelgum               London     GBR  53.344104   
6                              Mahalo          Culver City     USA  34.017606   
7                                Kyte        San Francisco     USA  37.788482   
8                                Veoh            San Diego     USA  32.902266   
9                              Wesabe        San Francisco     USA  37.793148   
10                    Jingle Networks             New York     USA  37.480999   
11                          Jangl SMS           Pleasanton     USA  37.697805   
12                              Jajah        Mountain View     USA  37.423390   
13                             blogTV            Ramat Gan     ISR  31.046051   
14                       AdaptiveBlue                  NYC     USA  40.801358   
15                     Pando Networks             New York     USA  40.722655   
16                         Livestream             New York     USA  40.726155   
17                            Ustream        San Francisco     USA  37.392936   
20                       GrandCentral              Fremont     USA  37.465645   
21                            YouTube            San Bruno     USA  37.627971   
22                             CastTV        San Francisco     USA  37.780716   
23                          SellABand        46395 Bocholt     DEU  51.808933   
24                           SodaHead               Encino     USA  37.269175   
25                          Revision3        San Francisco     USA  37.757758   
26                       Funny Or Die            San Mateo     USA  37.421621   
27                                EQO            Vancouver     CAN  49.263588   
28                             iSkoot            Cambridge     USA  42.375392   
29                             iSkoot        San Francisco     USA  37.780134   
30                         Pageflakes        San Francisco     USA  37.758113   
31                           Netvibes                Paris     FRA  48.870806   
33                         FeedBurner              Chicago     USA  41.889474   
34                               WeFi              Fairfax     USA  37.090240   
35                             TVtrip                Paris     FRA  48.856667   
36                               Bebo        San Francisco     USA  37.782103   
37                            RockYou         Redwood City     USA  37.484619   
38                            FlickIM             Berkeley     USA  37.870744   
39                             Loomia        San Francisco     USA  37.796396   
40                           Terabitz            Palo Alto     USA  37.437328   
41                              Meebo        Mountain View     USA  37.393679   
46                           Newsvine              Seattle     USA  47.618599   
47                         Eventbrite        San Francisco     USA  37.779507   
48                          coComment               Geneva     CHE  46.203810   
49                       Hotelicopter      Charlottesville     USA  38.030823   
50                             Zvents            San Mateo     USA  37.553121   
51                           Eventful            San Diego     USA  32.872081   
53                            Seesmic        San Francisco     USA  37.775196   
54                               ooma            Palo Alto     USA  37.451958   
55                           Flixster        San Francisco     USA  37.766909   
56                              oDesk         Redwood City     U

In [53]:
startup_clean.index = pd.RangeIndex(len(startup_clean.index))

In [54]:
startup_clean.head(30)

name            city country   latitude   longitude
0          Wetpaint         Seattle     USA  47.603122 -122.333253
1          Wetpaint        New York     USA  40.723731  -73.996431
2              Geni  West Hollywood     USA  34.090368 -118.393064
3           Slacker       San Diego     USA  33.022176 -117.081406
4             Joost        New York     USA  40.746497  -74.009447
5          Babelgum          London     GBR  53.344104   -6.267494
6            Mahalo     Culver City     USA  34.017606 -118.487267
7              Kyte   San Francisco     USA  37.788482 -122.409173
8              Veoh       San Diego     USA  32.902266 -117.208340
9            Wesabe   San Francisco     USA  37.793148 -122.402567
10  Jingle Networks        New York     USA  37.480999 -122.173887
11        Jangl SMS      Pleasanton     USA  37.697805 -121.907768
12            Jajah   Mountain View     USA  37.423390 -122.089951
13           blogTV       Ramat Gan     ISR  31.046051   34.851612
14     AdaptiveBlue             NYC     USA  40.801358  -74.337200
15   Pando Networks        New York     USA  40.722655  -73.998730
16       Livestream        New York     USA  40.726155  -73.995625
17          Ustream   San Francisco     USA  37.392936 -122.079480
18     GrandCentral         Fremont     USA  37.465645 -121.932202
19          YouTube       San Bruno     USA  37.627971 -122.426804
20           CastTV   San Francisco     USA  37.780716 -122.393913
21        SellABand   46395 Bocholt     DEU  51.808933    6.553452
22         SodaHead          Encino     USA  37.269175 -119.306607
23        Revision3   San Francisco     USA  37.757758 -122.388243
24     Funny Or Die       San Mateo     USA  37.421621 -122.137444
25              EQO       Vancouver     CAN  49.263588 -123.138565
26           iSkoot       Cambridge     USA  42.375392  -71.118487
27           iSkoot   San Francisco     USA  37.780134 -122.396744
28       Pageflakes   San Francisco     USA  37.758113 -122.414689
29         Netvibes           Paris     FRA  48.870806    2.346680

In [55]:
import folium

In [56]:
map_city=folium.Map(location=[40.7221,-73.9712], zoom_start=12)
for index, row in startup_clean.iterrows():
    folium.Marker((row['latitude'],row['longitude']),
                    radius=2,
                    icon=folium.Icon(icon='cloud',color='red'), 
                   ).add_to(map_city)
    


In [57]:
map_city

## APIs

In [58]:
import os
from dotenv import load_dotenv
import requests
load_dotenv()


True

In [59]:
def googleRequestAuthorized(lat,lon,r,keyword):

    # Function
    authToken = os.getenv("GOOGLE_API_TOKEN")
    if not authToken:
        raise ValueError("NECESITAS UN TOKEN")
    url = "https://maps.googleapis.com/maps/api/place/nearbysearch/json?location={},{}&radius={}&keyword={}&key={}".format(lat,lon,r,keyword,authToken)

    res = requests.get(url)
    data = res.json()
    return data

In [47]:
starbucks = googleRequestAuthorized("40.723731","-73.996431","200","starbucks")

In [23]:
vegan = googleRequestAuthorized("40.723731","-73.996431","200","vegan+restaurant")

In [49]:
club = googleRequestAuthorized("40.723731","-73.996431","500","club")

In [50]:
airport = googleRequestAuthorized("40.723731","-73.996431","30000","airport")

In [106]:
kindergarten = googleRequestAuthorized("40.723731","-73.996431","200","daycare")

In [24]:
l = vegan['results']

In [25]:
print(l[0]['name'])
print(l[0]['geometry']['location']['lat'])
print(l[0]['geometry']['location']['lng'])

by CHLOE.
40.7227818
-73.9972192


## There is a Starbucks in a radius of 100 meters

In [60]:
for i in range(len(startup_clean)) : 
    lat = startup_clean.loc[i, "latitude"]
    lon = startup_clean.loc[i, "longitude"]
    starbucks = googleRequestAuthorized(str(lat),str(lon),"100","starbucks")
    try:
        startup_clean.loc[i, 'starbucks'] = starbucks['results'][0]['name']
        startup_clean.loc[i, 'starbucks_lat'] = starbucks['results'][0]['geometry']['location']['lat']
        startup_clean.loc[i, 'starbucks_lon'] = starbucks['results'][0]['geometry']['location']['lng']

    except:
        startup_clean.loc[i, 'starbucks'] = np.nan
        startup_clean.loc[i, 'starbucks_lat'] = np.nan
        startup_clean.loc[i, 'starbucks_lon'] = np.nan

In [61]:
pd.set_option('display.max_rows', None)
display(startup_clean)

name                 city country   latitude  \
0                           Wetpaint              Seattle     USA  47.603122   
1                           Wetpaint             New York     USA  40.723731   
2                               Geni       West Hollywood     USA  34.090368   
3                            Slacker            San Diego     USA  33.022176   
4                              Joost             New York     USA  40.746497   
5                           Babelgum               London     GBR  53.344104   
6                             Mahalo          Culver City     USA  34.017606   
7                               Kyte        San Francisco     USA  37.788482   
8                               Veoh            San Diego     USA  32.902266   
9                             Wesabe        San Francisco     USA  37.793148   
10                   Jingle Networks             New York     USA  37.480999   
11                         Jangl SMS           Pleasanton     USA  37.697805   
12                             Jajah        Mountain View     USA  37.423390   
13                            blogTV            Ramat Gan     ISR  31.046051   
14                      AdaptiveBlue                  NYC     USA  40.801358   
15                    Pando Networks             New York     USA  40.722655   
16                        Livestream             New York     USA  40.726155   
17                           Ustream        San Francisco     USA  37.392936   
18                      GrandCentral              Fremont     USA  37.465645   
19                           YouTube            San Bruno     USA  37.627971   
20                            CastTV        San Francisco     USA  37.780716   
21                         SellABand        46395 Bocholt     DEU  51.808933   
22                          SodaHead               Encino     USA  37.269175   
23                         Revision3        San Francisco     USA  37.757758   
24                      Funny Or Die            San Mateo     USA  37.421621   
25                               EQO            Vancouver     CAN  49.263588   
26                            iSkoot            Cambridge     USA  42.375392   
27                            iSkoot        San Francisco     USA  37.780134   
28                        Pageflakes        San Francisco     USA  37.758113   
29                          Netvibes                Paris     FRA  48.870806   
30                        FeedBurner              Chicago     USA  41.889474   
31                              WeFi              Fairfax     USA  37.090240   
32                            TVtrip                Paris     FRA  48.856667   
33                              Bebo        San Francisco     USA  37.782103   
34                           RockYou         Redwood City     USA  37.484619   
35                           FlickIM             Berkeley     USA  37.870744   
36                            Loomia        San Francisco     USA  37.796396   
37                          Terabitz            Palo Alto     USA  37.437328   
38                             Meebo        Mountain View     USA  37.393679   
39                          Newsvine              Seattle     USA  47.618599   
40                        Eventbrite        San Francisco     USA  37.779507   
41                         coComment               Geneva     CHE  46.203810   
42                      Hotelicopter      Charlottesville     USA  38.030823   
43                            Zvents            San Mateo     USA  37.553121   
44                          Eventful            San Diego     USA  32.872081   
45                           Seesmic        San Francisco     USA  37.775196   
46                              ooma            Palo Alto     USA  37.451958   
47                          Flixster        San Francisco     USA  37.766909   
48                             oDesk         Redwood City     USA  37.479952   
49                           Goi

In [88]:
startup_clean.to_csv(r'./input/starbucks_with_nan.csv')

In [62]:
starbucks_clean = startup_clean.dropna()

In [63]:
starbucks_clean.index = pd.RangeIndex(len(starbucks_clean.index))

In [67]:
pd.set_option('display.max_rows', None)
display(starbucks_clean)

name                 city country   latitude  \
0                      Wetpaint              Seattle     USA  47.603122   
1                      Wetpaint             New York     USA  40.723731   
2                       Slacker            San Diego     USA  33.022176   
3                      Babelgum               London     GBR  53.344104   
4                        Mahalo          Culver City     USA  34.017606   
5                          Kyte        San Francisco     USA  37.788482   
6                        Wesabe        San Francisco     USA  37.793148   
7                  AdaptiveBlue                  NYC     USA  40.801358   
8                Pando Networks             New York     USA  40.722655   
9                    Livestream             New York     USA  40.726155   
10                      YouTube            San Bruno     USA  37.627971   
11                       CastTV        San Francisco     USA  37.780716   
12                          EQO            Vancouver     CAN  49.263588   
13                       iSkoot            Cambridge     USA  42.375392   
14                       iSkoot        San Francisco     USA  37.780134   
15                     Netvibes                Paris     FRA  48.870806   
16                   FeedBurner              Chicago     USA  41.889474   
17                         WeFi              Fairfax     USA  37.090240   
18                       TVtrip                Paris     FRA  48.856667   
19                         Bebo        San Francisco     USA  37.782103   
20                      FlickIM             Berkeley     USA  37.870744   
21                       Loomia        San Francisco     USA  37.796396   
22                     Terabitz            Palo Alto     USA  37.437328   
23                   Eventbrite        San Francisco     USA  37.779507   
24                      Seesmic        San Francisco     USA  37.775196   
25                     Flixster        San Francisco     USA  37.766909   
26                       spigit           Pleasanton     USA  37.663728   
27                       spigit               Reston     USA  38.959008   
28                       spigit               London     GBR  51.517038   
29                        Jaxtr           Menlo Park     USA  37.451026   
30                        Curse        San Francisco     USA  37.787092   
31                         Vuze            San Mateo     USA  37.485865   
32                    NowPublic            Vancouver     CAN  49.283376   
33                      Retrevo            Sunnyvale     USA  37.368594   
34                      Tangler        Mountain View     USA  37.386665   
35                       Revver          Los Angeles     USA  34.052187   
36                        Flock           Menlo Park     USA  37.491356   
37                      Dropbox        San Francisco     USA  37.790943   
38                   Kongregate        San Francisco     USA  37.786942   
39                     DanceJam        San Francisco     USA  37.781557   
40                         Yola        San Francisco     USA  37.791115   
41                     Filtrbox            Palo Alto     USA  40.010492   
42                   BitTorrent        San Francisco     USA  37.790998   
43                     Doostang            Palo Alto     USA  37.427235   
44                       Vlingo            Cambridge     USA  42.372912   
45                      Docstoc         Santa Monica     USA  34.018275   
46   Shock Treatment Management              Seattle     USA  47.610332   
47                       DotBlu        San Francisco     USA  37.090240   
48                        sezmi         Santa Monica     USA  34.017373   
49                   SpiralFrog             New York     USA  37.090240   
50                    MocoSpace               Boston     USA  42.350274   
51                    Thumbplay             New York     USA  40.725435   
52                        Wonga               London

In [66]:
starbucks_clean.to_csv(r'./input/starbucks_without_nan.csv')

## There is an airport in a radius of 20 km.

In [68]:
for i in range(len(starbucks_clean)) : 
    lat = starbucks_clean.loc[i, "latitude"]
    lon = starbucks_clean.loc[i, "longitude"]
    airport = googleRequestAuthorized(str(lat),str(lon),"20000","airport")
    try:
        starbucks_clean.loc[i, 'airport'] = airport['results'][0]['name']
        starbucks_clean.loc[i, 'air_lat'] = airport['results'][0]['geometry']['location']['lat']
        starbucks_clean.loc[i, 'air_lon'] = airport['results'][0]['geometry']['location']['lng']

    except:
        starbucks_clean.loc[i, 'airport'] = np.nan
        starbucks_clean.loc[i, 'air_lat'] = np.nan
        starbucks_clean.loc[i, 'air_lon'] = np.nan

In [72]:
pd.set_option('display.max_rows', None)
display(airports_clean)

name                 city country   latitude  \
0                      Wetpaint              Seattle     USA  47.603122   
1                      Wetpaint             New York     USA  40.723731   
2                       Slacker            San Diego     USA  33.022176   
3                      Babelgum               London     GBR  53.344104   
4                        Mahalo          Culver City     USA  34.017606   
5                          Kyte        San Francisco     USA  37.788482   
6                        Wesabe        San Francisco     USA  37.793148   
7                  AdaptiveBlue                  NYC     USA  40.801358   
8                Pando Networks             New York     USA  40.722655   
9                    Livestream             New York     USA  40.726155   
10                      YouTube            San Bruno     USA  37.627971   
11                       CastTV        San Francisco     USA  37.780716   
12                          EQO            Vancouver     CAN  49.263588   
13                       iSkoot            Cambridge     USA  42.375392   
14                       iSkoot        San Francisco     USA  37.780134   
15                     Netvibes                Paris     FRA  48.870806   
16                   FeedBurner              Chicago     USA  41.889474   
17                         WeFi              Fairfax     USA  37.090240   
18                       TVtrip                Paris     FRA  48.856667   
19                         Bebo        San Francisco     USA  37.782103   
20                      FlickIM             Berkeley     USA  37.870744   
21                       Loomia        San Francisco     USA  37.796396   
22                     Terabitz            Palo Alto     USA  37.437328   
23                   Eventbrite        San Francisco     USA  37.779507   
24                      Seesmic        San Francisco     USA  37.775196   
25                     Flixster        San Francisco     USA  37.766909   
26                       spigit           Pleasanton     USA  37.663728   
27                       spigit               Reston     USA  38.959008   
28                       spigit               London     GBR  51.517038   
29                        Jaxtr           Menlo Park     USA  37.451026   
30                        Curse        San Francisco     USA  37.787092   
31                         Vuze            San Mateo     USA  37.485865   
32                    NowPublic            Vancouver     CAN  49.283376   
33                      Retrevo            Sunnyvale     USA  37.368594   
34                      Tangler        Mountain View     USA  37.386665   
35                       Revver          Los Angeles     USA  34.052187   
36                        Flock           Menlo Park     USA  37.491356   
37                      Dropbox        San Francisco     USA  37.790943   
38                   Kongregate        San Francisco     USA  37.786942   
39                     DanceJam        San Francisco     USA  37.781557   
40                         Yola        San Francisco     USA  37.791115   
41                     Filtrbox            Palo Alto     USA  40.010492   
42                   BitTorrent        San Francisco     USA  37.790998   
43                     Doostang            Palo Alto     USA  37.427235   
44                       Vlingo            Cambridge     USA  42.372912   
45                      Docstoc         Santa Monica     USA  34.018275   
46   Shock Treatment Management              Seattle     USA  47.610332   
47                       DotBlu        San Francisco     USA  37.090240   
48                        sezmi         Santa Monica     USA  34.017373   
49                   SpiralFrog             New York     USA  37.090240   
50                    MocoSpace               Boston     USA  42.350274   
51                    Thumbplay             New York     USA  40.725435   
52                        Wonga               London

In [70]:
airports_clean = starbucks_clean.dropna()

In [71]:
airports_clean.index = pd.RangeIndex(len(airports_clean.index))

In [73]:
airports_clean.to_csv(r'./input/airports_without_nan.csv')

## There is a Day Care Center in a radius of 100 meters

In [74]:
def add_places(df,place,radius):
    for i in range(len(df)) : 
        lat = df.loc[i, "latitude"]
        lon = df.loc[i, "longitude"]
        answer = googleRequestAuthorized(str(lat),str(lon),str(radius),str(place))
        try:
            df.loc[i, str(place)] = answer['results'][0]['name']
            df.loc[i, str(place)+'_lat'] = answer['results'][0]['geometry']['location']['lat']
            df.loc[i, str(place)+'_lon'] = answer['results'][0]['geometry']['location']['lng']

        except:
            df.loc[i, str(place)] = np.nan
            df.loc[i, str(place)+'_lat'] = np.nan
            df.loc[i, str(place)+'_lon'] = np.nan

In [75]:
add_places(airports_clean,"daycare","100")

In [76]:
airports_clean

name                 city country   latitude  \
0                      Wetpaint              Seattle     USA  47.603122   
1                      Wetpaint             New York     USA  40.723731   
2                       Slacker            San Diego     USA  33.022176   
3                      Babelgum               London     GBR  53.344104   
4                        Mahalo          Culver City     USA  34.017606   
5                          Kyte        San Francisco     USA  37.788482   
6                        Wesabe        San Francisco     USA  37.793148   
7                  AdaptiveBlue                  NYC     USA  40.801358   
8                Pando Networks             New York     USA  40.722655   
9                    Livestream             New York     USA  40.726155   
10                      YouTube            San Bruno     USA  37.627971   
11                       CastTV        San Francisco     USA  37.780716   
12                          EQO            Vancouver     CAN  49.263588   
13                       iSkoot            Cambridge     USA  42.375392   
14                       iSkoot        San Francisco     USA  37.780134   
15                     Netvibes                Paris     FRA  48.870806   
16                   FeedBurner              Chicago     USA  41.889474   
17                         WeFi              Fairfax     USA  37.090240   
18                       TVtrip                Paris     FRA  48.856667   
19                         Bebo        San Francisco     USA  37.782103   
20                      FlickIM             Berkeley     USA  37.870744   
21                       Loomia        San Francisco     USA  37.796396   
22                     Terabitz            Palo Alto     USA  37.437328   
23                   Eventbrite        San Francisco     USA  37.779507   
24                      Seesmic        San Francisco     USA  37.775196   
25                     Flixster        San Francisco     USA  37.766909   
26                       spigit           Pleasanton     USA  37.663728   
27                       spigit               Reston     USA  38.959008   
28                       spigit               London     GBR  51.517038   
29                        Jaxtr           Menlo Park     USA  37.451026   
30                        Curse        San Francisco     USA  37.787092   
31                         Vuze            San Mateo     USA  37.485865   
32                    NowPublic            Vancouver     CAN  49.283376   
33                      Retrevo            Sunnyvale     USA  37.368594   
34                      Tangler        Mountain View     USA  37.386665   
35                       Revver          Los Angeles     USA  34.052187   
36                        Flock           Menlo Park     USA  37.491356   
37                      Dropbox        San Francisco     USA  37.790943   
38                   Kongregate        San Francisco     USA  37.786942   
39                     DanceJam        San Francisco     USA  37.781557   
40                         Yola        San Francisco     USA  37.791115   
41                     Filtrbox            Palo Alto     USA  40.010492   
42                   BitTorrent        San Francisco     USA  37.790998   
43                     Doostang            Palo Alto     USA  37.427235   
44                       Vlingo            Cambridge     USA  42.372912   
45                      Docstoc         Santa Monica     USA  34.018275   
46   Shock Treatment Management              Seattle     USA  47.610332   
47                       DotBlu        San Francisco     USA  37.090240   
48                        sezmi         Santa Monica     USA  34.017373   
49                   SpiralFrog             New York     USA  37.090240   
50                    MocoSpace               Boston     USA  42.350274   
51                    Thumbplay             New York     USA  40.725435   
52                        Wonga               London

In [77]:
daycare_clean = airports_clean.dropna()

In [78]:
daycare_clean.index = pd.RangeIndex(len(daycare_clean.index))

In [79]:
daycare_clean.to_csv(r'./input/daycare_without_nan.csv')

In [80]:
daycare_clean

name                 city country   latitude  \
0                      Wetpaint              Seattle     USA  47.603122   
1                        Wesabe        San Francisco     USA  37.793148   
2                Pando Networks             New York     USA  40.722655   
3                    Livestream             New York     USA  40.726155   
4                      Netvibes                Paris     FRA  48.870806   
5                    FeedBurner              Chicago     USA  41.889474   
6                        TVtrip                Paris     FRA  48.856667   
7                          Bebo        San Francisco     USA  37.782103   
8                        Loomia        San Francisco     USA  37.796396   
9                      Terabitz            Palo Alto     USA  37.437328   
10                   Eventbrite        San Francisco     USA  37.779507   
11                      Seesmic        San Francisco     USA  37.775196   
12                     Flixster        San Francisco     USA  37.766909   
13                       spigit               Reston     USA  38.959008   
14                        Curse        San Francisco     USA  37.787092   
15                         Vuze            San Mateo     USA  37.485865   
16                      Retrevo            Sunnyvale     USA  37.368594   
17                      Tangler        Mountain View     USA  37.386665   
18                       Revver          Los Angeles     USA  34.052187   
19                        Flock           Menlo Park     USA  37.491356   
20                      Dropbox        San Francisco     USA  37.790943   
21                   Kongregate        San Francisco     USA  37.786942   
22                         Yola        San Francisco     USA  37.791115   
23                   BitTorrent        San Francisco     USA  37.790998   
24                       Vlingo            Cambridge     USA  42.372912   
25                      Docstoc         Santa Monica     USA  34.018275   
26   Shock Treatment Management              Seattle     USA  47.610332   
27                    MocoSpace               Boston     USA  42.350274   
28                    Thumbplay             New York     USA  40.725435   
29                       OMGPOP             New York     USA  40.723384   
30                    RatePoint              Needham     USA  42.296111   
31                      Animoto             New York     USA  40.729480   
32                        Xobni        San Francisco     USA  37.789634   
33                    Worklight             New York     USA  40.756799   
34                      Mobivox             Montreal     CAN  45.500277   
35                         3Jam        San Francisco     USA  37.765125   
36                    Wikinvest        San Francisco     USA  37.775196   
37                     Polyvore        Mountain View     USA  37.386175   
38                       Tumblr             New York     USA  40.743808   
39                     EchoSign            Palo Alto     USA  37.445326   
40                    Eurekster                          USA  37.790992   
41                     Songbird        San Francisco     USA  37.787126   
42                       Disqus        San Francisco     USA  37.786906   
43                       Pelago              Seattle     USA  47.607065   
44                        Faves              Seattle     USA  47.603327   
45                       Plazes               Berlin     DEU  52.523402   
46                       Vringo             New York     USA  40.755001   
47                        Zmags           Copenhagen     DNK  55.683921   
48                   GameLayers        San Francisco     USA  37.803847   
49                       WEbook             New York     USA  38.984172   
50                    BeliefNet             New York     USA  40.740231   
51                     HubPages        San Francisco     USA  37.787695   
52                       Ribbit        Mountain View

## There is a nightclub in less than 200 meters

In [15]:
add_places(daycare_clean,"nightclub","200")

In [16]:
daycare_clean

Unnamed: 0                        name                 city country  \
0             0                    Wetpaint              Seattle     USA   
1             1                    Wetpaint             New York     USA   
2             2                      Mahalo          Culver City     USA   
3             3                        Kyte        San Francisco     USA   
4             4                      Wesabe        San Francisco     USA   
5             5                   Jangl SMS           Pleasanton     USA   
6             6              Pando Networks             New York     USA   
7             7                  Livestream             New York     USA   
8             8                     YouTube            San Bruno     USA   
9             9                      CastTV        San Francisco     USA   
10           10                         EQO            Vancouver     CAN   
11           11                      iSkoot            Cambridge     USA   
12           12                      iSkoot        San Francisco     USA   
13           13                    Netvibes                Paris     FRA   
14           14                  FeedBurner              Chicago     USA   
15           15                      TVtrip                Paris     FRA   
16           16                        Bebo        San Francisco     USA   
17           17                      Loomia        San Francisco     USA   
18           18                    Terabitz            Palo Alto     USA   
19           19                  Eventbrite        San Francisco     USA   
20           20                   coComment               Geneva     CHE   
21           21                      Zvents            San Mateo     USA   
22           22                    Eventful            San Diego     USA   
23           23                     Seesmic        San Francisco     USA   
24           24                    Flixster        San Francisco     USA   
25           25                     GoingOn        San Francisco     USA   
26           26                      spigit               Reston     USA   
27           27                      spigit               London     GBR   
28           28                 Respectance            San Mateo     USA   
29           29                       Curse        San Francisco     USA   
30           30                        Vuze            San Mateo     USA   
31           31                   NowPublic            Vancouver     CAN   
32           32                     Crackle          Culver City     USA   
33           33                     BuddyTV              Seattle     USA   
34           34                     Retrevo            Sunnyvale     USA   
35           35                     Tangler        Mountain View     USA   
36           36                      Revver          Los Angeles     USA   
37           37                       Flock           Menlo Park     USA   
38           38                     Dropbox        San Francisco     USA   
39           39                  Kongregate        San Francisco     USA   
40           40                    DanceJam        San Francisco     USA   
41           41                        Yola        San Francisco     USA   
42           42                  BitTorrent        San Francisco     USA   
43           43                    Doostang            Palo Alto     USA   
44           44                       Mevio        San Francisco     USA   
45           45                      Vlingo            Cambridge     USA   
46           46                     Docstoc         Santa Monica     USA   
47           47  Shock Treatment Management              Seattle     USA   
48           48                       sezmi         Santa Monica     USA   
49           49                   MocoSpace               Boston     USA   
50           50                   Minglebox            Bangalore     IND   
51           51                   Thumbplay          

In [17]:
nightclub_clean = daycare_clean.dropna()

In [18]:
nightclub_clean.index = pd.RangeIndex(len(nightclub_clean.index))

In [19]:
nightclub_clean

Unnamed: 0                        name                 city country  \
0             0                    Wetpaint              Seattle     USA   
1             1                    Wetpaint             New York     USA   
2             3                        Kyte        San Francisco     USA   
3             4                      Wesabe        San Francisco     USA   
4             5                   Jangl SMS           Pleasanton     USA   
5             6              Pando Networks             New York     USA   
6             7                  Livestream             New York     USA   
7             9                      CastTV        San Francisco     USA   
8            10                         EQO            Vancouver     CAN   
9            11                      iSkoot            Cambridge     USA   
10           12                      iSkoot        San Francisco     USA   
11           13                    Netvibes                Paris     FRA   
12           14                  FeedBurner              Chicago     USA   
13           15                      TVtrip                Paris     FRA   
14           16                        Bebo        San Francisco     USA   
15           17                      Loomia        San Francisco     USA   
16           19                  Eventbrite        San Francisco     USA   
17           20                   coComment               Geneva     CHE   
18           21                      Zvents            San Mateo     USA   
19           23                     Seesmic        San Francisco     USA   
20           24                    Flixster        San Francisco     USA   
21           25                     GoingOn        San Francisco     USA   
22           26                      spigit               Reston     USA   
23           27                      spigit               London     GBR   
24           28                 Respectance            San Mateo     USA   
25           29                       Curse        San Francisco     USA   
26           30                        Vuze            San Mateo     USA   
27           31                   NowPublic            Vancouver     CAN   
28           32                     Crackle          Culver City     USA   
29           35                     Tangler        Mountain View     USA   
30           36                      Revver          Los Angeles     USA   
31           37                       Flock           Menlo Park     USA   
32           38                     Dropbox        San Francisco     USA   
33           39                  Kongregate        San Francisco     USA   
34           40                    DanceJam        San Francisco     USA   
35           41                        Yola        San Francisco     USA   
36           42                  BitTorrent        San Francisco     USA   
37           43                    Doostang            Palo Alto     USA   
38           44                       Mevio        San Francisco     USA   
39           45                      Vlingo            Cambridge     USA   
40           46                     Docstoc         Santa Monica     USA   
41           47  Shock Treatment Management              Seattle     USA   
42           49                   MocoSpace               Boston     USA   
43           50                   Minglebox            Bangalore     IND   
44           51                   Thumbplay             New York     USA   
45           52                       Wonga               London     GBR   
46           53                      SayNow            Palo Alto     USA   
47           54                 Crunchyroll        San Francisco     USA   
48           55                      OMGPOP             New York     USA   
49           56                     Behance             New York     USA   
50           57                    FlowPlay              Seattle     USA   
51           58                  Viewpoints          

In [26]:
nightclub_clean.to_csv(r'./input/nightclub_without_nan.csv')

## There is a vegan restaurant in a radius of 200 meters

In [27]:
add_places(nightclub_clean,"vegan+restaurant","200")

/home/mariobru/.local/lib/python3.6/site-packages/pandas/core/indexing.py:376: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[key] = _infer_fill_value(value)
/home/mariobru/.local/lib/python3.6/site-packages/pandas/core/indexing.py:494: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[item] = s


In [28]:
nightclub_clean

Unnamed: 0                        name                 city country  \
0             0                    Wetpaint              Seattle     USA   
1             1                    Wetpaint             New York     USA   
2             3                        Kyte        San Francisco     USA   
3             4                      Wesabe        San Francisco     USA   
4             5                   Jangl SMS           Pleasanton     USA   
5             6              Pando Networks             New York     USA   
6             7                  Livestream             New York     USA   
7             9                      CastTV        San Francisco     USA   
8            10                         EQO            Vancouver     CAN   
9            11                      iSkoot            Cambridge     USA   
10           12                      iSkoot        San Francisco     USA   
11           13                    Netvibes                Paris     FRA   
12           14                  FeedBurner              Chicago     USA   
13           15                      TVtrip                Paris     FRA   
14           16                        Bebo        San Francisco     USA   
15           17                      Loomia        San Francisco     USA   
16           19                  Eventbrite        San Francisco     USA   
17           20                   coComment               Geneva     CHE   
18           21                      Zvents            San Mateo     USA   
19           23                     Seesmic        San Francisco     USA   
20           24                    Flixster        San Francisco     USA   
21           25                     GoingOn        San Francisco     USA   
22           26                      spigit               Reston     USA   
23           27                      spigit               London     GBR   
24           28                 Respectance            San Mateo     USA   
25           29                       Curse        San Francisco     USA   
26           30                        Vuze            San Mateo     USA   
27           31                   NowPublic            Vancouver     CAN   
28           32                     Crackle          Culver City     USA   
29           35                     Tangler        Mountain View     USA   
30           36                      Revver          Los Angeles     USA   
31           37                       Flock           Menlo Park     USA   
32           38                     Dropbox        San Francisco     USA   
33           39                  Kongregate        San Francisco     USA   
34           40                    DanceJam        San Francisco     USA   
35           41                        Yola        San Francisco     USA   
36           42                  BitTorrent        San Francisco     USA   
37           43                    Doostang            Palo Alto     USA   
38           44                       Mevio        San Francisco     USA   
39           45                      Vlingo            Cambridge     USA   
40           46                     Docstoc         Santa Monica     USA   
41           47  Shock Treatment Management              Seattle     USA   
42           49                   MocoSpace               Boston     USA   
43           50                   Minglebox            Bangalore     IND   
44           51                   Thumbplay             New York     USA   
45           52                       Wonga               London     GBR   
46           53                      SayNow            Palo Alto     USA   
47           54                 Crunchyroll        San Francisco     USA   
48           55                      OMGPOP             New York     USA   
49           56                     Behance             New York     USA   
50           57                    FlowPlay              Seattle     USA   
51           58                  Viewpoints          

In [29]:
all_clean = nightclub_clean.dropna()

In [30]:
all_clean.index = pd.RangeIndex(len(all_clean.index))

In [31]:
all_clean.to_csv(r'./input/all_clean.csv')

In [32]:
all_clean

Unnamed: 0                        name                 city country  \
0             0                    Wetpaint              Seattle     USA   
1             1                    Wetpaint             New York     USA   
2             3                        Kyte        San Francisco     USA   
3             4                      Wesabe        San Francisco     USA   
4             5                   Jangl SMS           Pleasanton     USA   
5             6              Pando Networks             New York     USA   
6             7                  Livestream             New York     USA   
7             9                      CastTV        San Francisco     USA   
8            10                         EQO            Vancouver     CAN   
9            11                      iSkoot            Cambridge     USA   
10           12                      iSkoot        San Francisco     USA   
11           13                    Netvibes                Paris     FRA   
12           14                  FeedBurner              Chicago     USA   
13           15                      TVtrip                Paris     FRA   
14           16                        Bebo        San Francisco     USA   
15           17                      Loomia        San Francisco     USA   
16           19                  Eventbrite        San Francisco     USA   
17           20                   coComment               Geneva     CHE   
18           23                     Seesmic        San Francisco     USA   
19           24                    Flixster        San Francisco     USA   
20           25                     GoingOn        San Francisco     USA   
21           26                      spigit               Reston     USA   
22           27                      spigit               London     GBR   
23           29                       Curse        San Francisco     USA   
24           30                        Vuze            San Mateo     USA   
25           31                   NowPublic            Vancouver     CAN   
26           32                     Crackle          Culver City     USA   
27           35                     Tangler        Mountain View     USA   
28           36                      Revver          Los Angeles     USA   
29           37                       Flock           Menlo Park     USA   
30           38                     Dropbox        San Francisco     USA   
31           39                  Kongregate        San Francisco     USA   
32           40                    DanceJam        San Francisco     USA   
33           41                        Yola        San Francisco     USA   
34           42                  BitTorrent        San Francisco     USA   
35           43                    Doostang            Palo Alto     USA   
36           44                       Mevio        San Francisco     USA   
37           45                      Vlingo            Cambridge     USA   
38           46                     Docstoc         Santa Monica     USA   
39           47  Shock Treatment Management              Seattle     USA   
40           49                   MocoSpace               Boston     USA   
41           50                   Minglebox            Bangalore     IND   
42           51                   Thumbplay             New York     USA   
43           52                       Wonga               London     GBR   
44           53                      SayNow            Palo Alto     USA   
45           54                 Crunchyroll        San Francisco     USA   
46           55                      OMGPOP             New York     USA   
47           56                     Behance             New York     USA   
48           57                    FlowPlay              Seattle     USA   
49           58                  Viewpoints              Chicago     USA   
50           59                   RatePoint              Needham     USA   
51           60                       mig33          

In [33]:
city_count = all_clean.groupby(['city']).count()


In [34]:
city_count

Unnamed: 0  name  country  latitude  longitude  \
city                                                                  
Amsterdam                     2     2        2         2          2   
Austin                        2     2        2         2          2   
Bangalore                     4     4        4         4          4   
Barcelona                     2     2        2         2          2   
Bellevue                      3     3        3         3          3   
Belmont                       1     1        1         1          1   
Berkeley                      1     1        1         1          1   
Berlin                        2     2        2         2          2   
Beverly Hills                 1     1        1         1          1   
Birmingham                    1     1        1         1          1   
Boston                        6     6        6         6          6   
Boulder                       4     4        4         4          4   
Brooklyn                      2     2        2         2          2   
Budapest                      1     1        1         1          1   
Burlingame                    1     1        1         1          1   
Burlington                    3     3        3         3          3   
Cambridge                    10    10       10        10         10   
Capital Federal               1     1        1         1          1   
Chicago                       7     7        7         7          7   
Colorado Springs              1     1        1         1          1   
Copenhagen                    1     1        1         1          1   
Copenhagen V                  1     1        1         1          1   
Corte Madera                  2     2        2         2          2   
Culver City                   1     1        1         1          1   
Cupertino                     1     1        1         1          1   
Dublin                        2     2        2         2          2   
El Segundo                    2     2        2         2          2   
Emeryville                    1     1        1         1          1   
Fort Lauderdale               1     1        1         1          1   
Foster City                   3     3        3         3          3   
Freedom                       1     1        1         1          1   
Gainesville                   1     1        1         1          1   
Geneva                        1     1        1         1          1   
Glen Cove                     1     1        1         1          1   
Greenbelt                     1     1        1         1          1   
Halifax                       1     1        1         1          1   
Hamburg                       1     1        1         1          1   
Honolulu                      1     1        1         1          1   
Irvington                     1     1        1         1          1   
Kitchener                     1     1        1         1          1   
La Jolla                      1     1        1         1          1   
Lancaster                     1     1        1         1          1   
London                       13    13       13        13         13   
Longmont                      1     1        1         1          1   
Los Angeles                   5     5        5         5          5   
McLean                        1     1        1         1          1   
Melbourne, Victoria           1     1        1         1          1   
Menlo Park                    4     4        4         4          4   
Mexico City                   1     1        1         1          1   
Milan                         1     1        1         1          1   
Montreal                      1     1        1         1          1   
Montreal, Quebec              1     1        1         1          1   
MontrÃ©al, Qc                 1     1        1         1          1   
Mountain View                 5     5        5         5          5   
Nangor Road                   1     1        

In [38]:
city_sorted = city_count.sort_values(['name'], ascending=[False]).head(30)


In [39]:
city_sorted['name']

city
San Francisco    83
New York         59
Seattle          19
London           13
Palo Alto        12
Cambridge        10
Paris             7
Chicago           7
Boston            6
Sunnyvale         5
Los Angeles       5
Mountain View     5
Santa Monica      4
San Mateo         4
Bangalore         4
New York City     4
Menlo Park        4
Boulder           4
Burlington        3
Singapore         3
San Jose          3
Redwood City      3
Bellevue          3
Toronto           3
Foster City       3
Vancouver         3
Pleasanton        2
Reston            2
San Francsico     2
San Diego         2
Name: name, dtype: int64